Feature Map Compression & Decompression with ZFP
=============================================

In [1]:
%matplotlib inline
import keras
import numpy as np
import pandas as pd
import os
import math
import scipy
import pickle
import cv2
import matplotlib.pyplot as plt

from keras.models import Model, Sequential
from keras.applications.vgg19 import VGG19
from keras.preprocessing.image import load_img
from keras.preprocessing.image import img_to_array
from keras.applications.imagenet_utils import preprocess_input, decode_predictions

from PIL import Image
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.model_selection import StratifiedShuffleSplit

from scipy.stats import binom
from scipy.misc import imread
from scipy.misc import imresize

from pyzfp import compress, decompress

Using TensorFlow backend.


In [2]:
# Load VGG19 Model
pre_trained_vgg = VGG19(weights='imagenet')

In [5]:
# Load the pickle file for obtaining the classes
DAT_FILE_PATH = "ImageNet/imagenet-classes-dict.dat"
pickle_in = open(DAT_FILE_PATH, "rb")
classes_dict = pickle.load(pickle_in)

In [6]:
# Load validation set ground truth labels
LABELS_FILE_PATH = 'ImageNet/ILSVRC2012_validation_ground_truth.txt'
y = np.loadtxt(LABELS_FILE_PATH, skiprows=0)

In [7]:
# Get .JPEG file names
DIR_PATH = "ImageNet/val_data/"
filelist = os.listdir(DIR_PATH)
filelist = sorted(filelist)

Original VGG19 Accuracy
------------------------------------

In [8]:
# Predict the probabilities and labels for each validation sample
predict_prob = []
predict_label = []

for i in range(50000):

    filename = DIR_PATH + filelist[i]
    # load an image in PIL format
    original = load_img(filename)
    #print(K.image_data_format())
    #print('PIL image size',original.size)
    #plt.imshow(original)
    #plt.show()

    aspect_ratio = original.size[0]/original.size[1]
    
    if original.size[0] < original.size[1]:
        width = 256
        height = width/aspect_ratio
    else:
        height = 256
        width = height * aspect_ratio
    
    original = original.resize((int(width), int(height)))
        
    
    width, height = original.size   # Get dimensions

    left = (width - 224)/2
    top = (height - 224)/2
    right = (width + 224)/2
    bottom = (height + 224)/2

    original = original.crop((left, top, right, bottom))
    
    # convert the PIL image to a numpy array
    # IN PIL - image is in (width, height, channel)
    # In Numpy - image is in (height, width, channel)
    numpy_image = img_to_array(original)
    
    # Convert the image / images into batch format
    # expand_dims will add an extra dimension to the data at a particular axis
    # We want the input matrix to the network to be of the form (batchsize, height, width, channels)
    # Thus we add the extra dimension to the axis 0.
    image_batch = np.expand_dims(numpy_image, axis=0)
    

    # prepare the image for the VGG model
    processed_image = preprocess_input(image_batch)
    
    # get the predicted probabilities for each class
    predictions = pre_trained_vgg.predict(processed_image)
    label = decode_predictions(predictions)
    predict_prob.append(np.max(predictions))
    predict_label.append(classes_dict[label[0][0][0]])
    print("Iteration: ", i, "Predict: ", classes_dict[label[0][0][0]], "Ground Truth: ", y[i])

Iteration:  0 Predict:  487 Ground Truth:  490.0
Iteration:  1 Predict:  590 Ground Truth:  361.0
Iteration:  2 Predict:  171 Ground Truth:  171.0
Iteration:  3 Predict:  822 Ground Truth:  822.0
Iteration:  4 Predict:  297 Ground Truth:  297.0
Iteration:  5 Predict:  490 Ground Truth:  482.0
Iteration:  6 Predict:  13 Ground Truth:  13.0
Iteration:  7 Predict:  970 Ground Truth:  704.0
Iteration:  8 Predict:  599 Ground Truth:  599.0
Iteration:  9 Predict:  10 Ground Truth:  164.0
Iteration:  10 Predict:  649 Ground Truth:  649.0
Iteration:  11 Predict:  11 Ground Truth:  11.0
Iteration:  12 Predict:  73 Ground Truth:  73.0
Iteration:  13 Predict:  286 Ground Truth:  286.0
Iteration:  14 Predict:  554 Ground Truth:  554.0
Iteration:  15 Predict:  6 Ground Truth:  6.0
Iteration:  16 Predict:  591 Ground Truth:  648.0
Iteration:  17 Predict:  397 Ground Truth:  399.0
Iteration:  18 Predict:  749 Ground Truth:  749.0
Iteration:  19 Predict:  545 Ground Truth:  545.0
Iteration:  20 Predic

Iteration:  164 Predict:  737 Ground Truth:  737.0
Iteration:  165 Predict:  333 Ground Truth:  333.0
Iteration:  166 Predict:  729 Ground Truth:  729.0
Iteration:  167 Predict:  824 Ground Truth:  824.0
Iteration:  168 Predict:  517 Ground Truth:  517.0
Iteration:  169 Predict:  89 Ground Truth:  89.0
Iteration:  170 Predict:  724 Ground Truth:  724.0
Iteration:  171 Predict:  2 Ground Truth:  2.0
Iteration:  172 Predict:  829 Ground Truth:  829.0
Iteration:  173 Predict:  172 Ground Truth:  172.0
Iteration:  174 Predict:  266 Ground Truth:  266.0
Iteration:  175 Predict:  109 Ground Truth:  123.0
Iteration:  176 Predict:  434 Ground Truth:  434.0
Iteration:  177 Predict:  149 Ground Truth:  149.0
Iteration:  178 Predict:  39 Ground Truth:  39.0
Iteration:  179 Predict:  128 Ground Truth:  171.0
Iteration:  180 Predict:  148 Ground Truth:  44.0
Iteration:  181 Predict:  771 Ground Truth:  662.0
Iteration:  182 Predict:  734 Ground Truth:  734.0
Iteration:  183 Predict:  985 Ground Tru

Iteration:  326 Predict:  64 Ground Truth:  42.0
Iteration:  327 Predict:  397 Ground Truth:  397.0
Iteration:  328 Predict:  384 Ground Truth:  383.0
Iteration:  329 Predict:  720 Ground Truth:  720.0
Iteration:  330 Predict:  753 Ground Truth:  668.0
Iteration:  331 Predict:  738 Ground Truth:  738.0
Iteration:  332 Predict:  143 Ground Truth:  143.0
Iteration:  333 Predict:  994 Ground Truth:  923.0
Iteration:  334 Predict:  843 Ground Truth:  843.0
Iteration:  335 Predict:  820 Ground Truth:  820.0
Iteration:  336 Predict:  487 Ground Truth:  485.0
Iteration:  337 Predict:  790 Ground Truth:  790.0
Iteration:  338 Predict:  914 Ground Truth:  529.0
Iteration:  339 Predict:  37 Ground Truth:  37.0
Iteration:  340 Predict:  848 Ground Truth:  848.0
Iteration:  341 Predict:  626 Ground Truth:  626.0
Iteration:  342 Predict:  186 Ground Truth:  186.0
Iteration:  343 Predict:  761 Ground Truth:  761.0
Iteration:  344 Predict:  544 Ground Truth:  593.0
Iteration:  345 Predict:  302 Groun

Iteration:  488 Predict:  789 Ground Truth:  789.0
Iteration:  489 Predict:  714 Ground Truth:  714.0
Iteration:  490 Predict:  830 Ground Truth:  830.0
Iteration:  491 Predict:  52 Ground Truth:  441.0
Iteration:  492 Predict:  966 Ground Truth:  966.0
Iteration:  493 Predict:  767 Ground Truth:  767.0
Iteration:  494 Predict:  100 Ground Truth:  100.0
Iteration:  495 Predict:  6 Ground Truth:  6.0
Iteration:  496 Predict:  502 Ground Truth:  502.0
Iteration:  497 Predict:  495 Ground Truth:  495.0
Iteration:  498 Predict:  547 Ground Truth:  547.0
Iteration:  499 Predict:  31 Ground Truth:  31.0
Iteration:  500 Predict:  102 Ground Truth:  102.0
Iteration:  501 Predict:  53 Ground Truth:  53.0
Iteration:  502 Predict:  675 Ground Truth:  315.0
Iteration:  503 Predict:  834 Ground Truth:  834.0
Iteration:  504 Predict:  592 Ground Truth:  592.0
Iteration:  505 Predict:  301 Ground Truth:  301.0
Iteration:  506 Predict:  141 Ground Truth:  141.0
Iteration:  507 Predict:  507 Ground Tru

Iteration:  650 Predict:  386 Ground Truth:  386.0
Iteration:  651 Predict:  695 Ground Truth:  596.0
Iteration:  652 Predict:  970 Ground Truth:  970.0
Iteration:  653 Predict:  788 Ground Truth:  777.0
Iteration:  654 Predict:  216 Ground Truth:  216.0
Iteration:  655 Predict:  783 Ground Truth:  783.0
Iteration:  656 Predict:  169 Ground Truth:  169.0
Iteration:  657 Predict:  148 Ground Truth:  148.0
Iteration:  658 Predict:  699 Ground Truth:  269.0
Iteration:  659 Predict:  313 Ground Truth:  228.0
Iteration:  660 Predict:  131 Ground Truth:  147.0
Iteration:  661 Predict:  227 Ground Truth:  227.0
Iteration:  662 Predict:  252 Ground Truth:  252.0
Iteration:  663 Predict:  564 Ground Truth:  244.0
Iteration:  664 Predict:  5 Ground Truth:  5.0
Iteration:  665 Predict:  709 Ground Truth:  544.0
Iteration:  666 Predict:  376 Ground Truth:  219.0
Iteration:  667 Predict:  139 Ground Truth:  139.0
Iteration:  668 Predict:  628 Ground Truth:  612.0
Iteration:  669 Predict:  686 Groun

...

Iteration:  49308 Predict:  798 Ground Truth:  798.0
Iteration:  49309 Predict:  738 Ground Truth:  738.0
Iteration:  49310 Predict:  486 Ground Truth:  486.0
Iteration:  49311 Predict:  794 Ground Truth:  794.0
Iteration:  49312 Predict:  453 Ground Truth:  408.0
Iteration:  49313 Predict:  940 Ground Truth:  940.0
Iteration:  49314 Predict:  422 Ground Truth:  422.0
Iteration:  49315 Predict:  878 Ground Truth:  501.0
Iteration:  49316 Predict:  905 Ground Truth:  905.0
Iteration:  49317 Predict:  770 Ground Truth:  770.0
Iteration:  49318 Predict:  821 Ground Truth:  821.0
Iteration:  49319 Predict:  108 Ground Truth:  108.0
Iteration:  49320 Predict:  376 Ground Truth:  376.0
Iteration:  49321 Predict:  592 Ground Truth:  592.0
Iteration:  49322 Predict:  104 Ground Truth:  104.0
Iteration:  49323 Predict:  189 Ground Truth:  189.0
Iteration:  49324 Predict:  822 Ground Truth:  844.0
Iteration:  49325 Predict:  191 Ground Truth:  191.0
Iteration:  49326 Predict:  60 Ground Truth:  

Iteration:  49464 Predict:  296 Ground Truth:  296.0
Iteration:  49465 Predict:  608 Ground Truth:  608.0
Iteration:  49466 Predict:  561 Ground Truth:  664.0
Iteration:  49467 Predict:  924 Ground Truth:  924.0
Iteration:  49468 Predict:  908 Ground Truth:  908.0
Iteration:  49469 Predict:  795 Ground Truth:  537.0
Iteration:  49470 Predict:  85 Ground Truth:  85.0
Iteration:  49471 Predict:  993 Ground Truth:  993.0
Iteration:  49472 Predict:  559 Ground Truth:  559.0
Iteration:  49473 Predict:  707 Ground Truth:  671.0
Iteration:  49474 Predict:  235 Ground Truth:  243.0
Iteration:  49475 Predict:  921 Ground Truth:  921.0
Iteration:  49476 Predict:  190 Ground Truth:  190.0
Iteration:  49477 Predict:  604 Ground Truth:  606.0
Iteration:  49478 Predict:  508 Ground Truth:  508.0
Iteration:  49479 Predict:  429 Ground Truth:  432.0
Iteration:  49480 Predict:  997 Ground Truth:  997.0
Iteration:  49481 Predict:  708 Ground Truth:  708.0
Iteration:  49482 Predict:  201 Ground Truth:  2

Iteration:  49621 Predict:  803 Ground Truth:  803.0
Iteration:  49622 Predict:  514 Ground Truth:  991.0
Iteration:  49623 Predict:  730 Ground Truth:  630.0
Iteration:  49624 Predict:  984 Ground Truth:  984.0
Iteration:  49625 Predict:  982 Ground Truth:  982.0
Iteration:  49626 Predict:  133 Ground Truth:  133.0
Iteration:  49627 Predict:  264 Ground Truth:  264.0
Iteration:  49628 Predict:  34 Ground Truth:  34.0
Iteration:  49629 Predict:  902 Ground Truth:  902.0
Iteration:  49630 Predict:  55 Ground Truth:  76.0
Iteration:  49631 Predict:  317 Ground Truth:  317.0
Iteration:  49632 Predict:  708 Ground Truth:  708.0
Iteration:  49633 Predict:  277 Ground Truth:  277.0
Iteration:  49634 Predict:  469 Ground Truth:  469.0
Iteration:  49635 Predict:  182 Ground Truth:  48.0
Iteration:  49636 Predict:  499 Ground Truth:  499.0
Iteration:  49637 Predict:  631 Ground Truth:  632.0
Iteration:  49638 Predict:  400 Ground Truth:  400.0
Iteration:  49639 Predict:  207 Ground Truth:  207.

Iteration:  49777 Predict:  20 Ground Truth:  20.0
Iteration:  49778 Predict:  180 Ground Truth:  180.0
Iteration:  49779 Predict:  81 Ground Truth:  23.0
Iteration:  49780 Predict:  74 Ground Truth:  74.0
Iteration:  49781 Predict:  462 Ground Truth:  462.0
Iteration:  49782 Predict:  425 Ground Truth:  425.0
Iteration:  49783 Predict:  869 Ground Truth:  869.0
Iteration:  49784 Predict:  753 Ground Truth:  536.0
Iteration:  49785 Predict:  833 Ground Truth:  833.0
Iteration:  49786 Predict:  921 Ground Truth:  810.0
Iteration:  49787 Predict:  61 Ground Truth:  61.0
Iteration:  49788 Predict:  282 Ground Truth:  281.0
Iteration:  49789 Predict:  572 Ground Truth:  572.0
Iteration:  49790 Predict:  702 Ground Truth:  702.0
Iteration:  49791 Predict:  196 Ground Truth:  196.0
Iteration:  49792 Predict:  955 Ground Truth:  955.0
Iteration:  49793 Predict:  702 Ground Truth:  990.0
Iteration:  49794 Predict:  755 Ground Truth:  755.0
Iteration:  49795 Predict:  768 Ground Truth:  768.0
I

Iteration:  49934 Predict:  922 Ground Truth:  922.0
Iteration:  49935 Predict:  448 Ground Truth:  448.0
Iteration:  49936 Predict:  421 Ground Truth:  421.0
Iteration:  49937 Predict:  670 Ground Truth:  670.0
Iteration:  49938 Predict:  127 Ground Truth:  127.0
Iteration:  49939 Predict:  579 Ground Truth:  579.0
Iteration:  49940 Predict:  532 Ground Truth:  800.0
Iteration:  49941 Predict:  128 Ground Truth:  128.0
Iteration:  49942 Predict:  690 Ground Truth:  690.0
Iteration:  49943 Predict:  334 Ground Truth:  334.0
Iteration:  49944 Predict:  817 Ground Truth:  854.0
Iteration:  49945 Predict:  818 Ground Truth:  530.0
Iteration:  49946 Predict:  337 Ground Truth:  337.0
Iteration:  49947 Predict:  188 Ground Truth:  129.0
Iteration:  49948 Predict:  924 Ground Truth:  924.0
Iteration:  49949 Predict:  769 Ground Truth:  769.0
Iteration:  49950 Predict:  983 Ground Truth:  819.0
Iteration:  49951 Predict:  702 Ground Truth:  220.0
Iteration:  49952 Predict:  756 Ground Truth: 

In [9]:
# Convert predict_prob, predict_label to numpy arrays
predict_prob = np.array(predict_prob)
predict_label = np.array(predict_label)

# 0 for correct prediction and 1 for wrong prediction
residuals = (predict_label!=y)

In [10]:
# Check the accuracy
Accuracy = ((50000 - sum(residuals))/50000)*100

print("Top-1 Accuracy is: ", Accuracy)

Top-1 Accuracy is:  70.86


Evaluate accuracy after compressing and decompressing an arbitrary intermediate layer
------------------------------------------------------------------------------------------------------------------------------

In [11]:
for layer in pre_trained_vgg.layers:
    print(layer.name)

input_1
block1_conv1
block1_conv2
block1_pool
block2_conv1
block2_conv2
block2_pool
block3_conv1
block3_conv2
block3_conv3
block3_conv4
block3_pool
block4_conv1
block4_conv2
block4_conv3
block4_conv4
block4_pool
block5_conv1
block5_conv2
block5_conv3
block5_conv4
block5_pool
flatten
fc1
fc2
predictions


In [13]:
predict_prob = []
predict_label = []

# Set tolerance and parallel mode for compression
tolerance = 0.0000001
parallel = True

for i in range(50000):

    filename = DIR_PATH + filelist[i]
    original = load_img(filename)
    aspect_ratio = original.size[0]/original.size[1]
    
    if original.size[0] < original.size[1]:
        width = 256
        height = width/aspect_ratio
    else:
        height = 256
        width = height * aspect_ratio
    
    original = original.resize((int(width), int(height)))
    width, height = original.size
    left = (width - 224)/2
    top = (height - 224)/2
    right = (width + 224)/2
    bottom = (height + 224)/2
    original = original.crop((left, top, right, bottom))
    
    numpy_image = img_to_array(original)
    image_batch = np.expand_dims(numpy_image, axis=0)
    
    processed_image = preprocess_input(image_batch)
    
    # Extract feature map from an arbitrary intermediate layer[MaxPool_4]
    model_head = Model(inputs=pre_trained_vgg.input, outputs=pre_trained_vgg.get_layer('block4_pool').output)
    block4_pool_features = model_head.predict(processed_image)
    
    # Compress and decompress the extracted feature map
    tmp = block4_pool_features[0,:,:,:]
    compressed = compress(tmp, tolerance=tolerance, parallel=parallel)
    recovered = decompress(compressed, tmp.shape, tmp.dtype, tolerance=tolerance)
    e = np.expand_dims(recovered,0)
    
    model_tail = Sequential()
    for a in range(17, 26):
        model_tail.add(pre_trained_vgg.layers[a])
    
    # get the predicted probabilities for each class
    predictions = model_tail.predict(e)
    label = decode_predictions(predictions)
    predict_prob.append(np.max(predictions))
    predict_label.append(classes_dict[label[0][0][0]])
    print("Iteration: ", i, "Predict: ", classes_dict[label[0][0][0]], "Ground Truth: ", y[i])

Iteration:  0 Predict:  487 Ground Truth:  490.0
Iteration:  1 Predict:  590 Ground Truth:  361.0
Iteration:  2 Predict:  171 Ground Truth:  171.0
Iteration:  3 Predict:  822 Ground Truth:  822.0
Iteration:  4 Predict:  297 Ground Truth:  297.0
Iteration:  5 Predict:  490 Ground Truth:  482.0
Iteration:  6 Predict:  13 Ground Truth:  13.0
Iteration:  7 Predict:  970 Ground Truth:  704.0
Iteration:  8 Predict:  599 Ground Truth:  599.0
Iteration:  9 Predict:  10 Ground Truth:  164.0
Iteration:  10 Predict:  649 Ground Truth:  649.0
Iteration:  11 Predict:  11 Ground Truth:  11.0
Iteration:  12 Predict:  73 Ground Truth:  73.0
Iteration:  13 Predict:  286 Ground Truth:  286.0
Iteration:  14 Predict:  554 Ground Truth:  554.0
Iteration:  15 Predict:  6 Ground Truth:  6.0
Iteration:  16 Predict:  591 Ground Truth:  648.0
Iteration:  17 Predict:  397 Ground Truth:  399.0
Iteration:  18 Predict:  749 Ground Truth:  749.0
Iteration:  19 Predict:  545 Ground Truth:  545.0
Iteration:  20 Predic

Iteration:  164 Predict:  737 Ground Truth:  737.0
Iteration:  165 Predict:  333 Ground Truth:  333.0
Iteration:  166 Predict:  729 Ground Truth:  729.0
Iteration:  167 Predict:  824 Ground Truth:  824.0
Iteration:  168 Predict:  517 Ground Truth:  517.0
Iteration:  169 Predict:  89 Ground Truth:  89.0
Iteration:  170 Predict:  724 Ground Truth:  724.0
Iteration:  171 Predict:  2 Ground Truth:  2.0
Iteration:  172 Predict:  829 Ground Truth:  829.0
Iteration:  173 Predict:  172 Ground Truth:  172.0
Iteration:  174 Predict:  266 Ground Truth:  266.0
Iteration:  175 Predict:  109 Ground Truth:  123.0
Iteration:  176 Predict:  434 Ground Truth:  434.0
Iteration:  177 Predict:  149 Ground Truth:  149.0
Iteration:  178 Predict:  39 Ground Truth:  39.0
Iteration:  179 Predict:  128 Ground Truth:  171.0
Iteration:  180 Predict:  148 Ground Truth:  44.0
Iteration:  181 Predict:  771 Ground Truth:  662.0
Iteration:  182 Predict:  734 Ground Truth:  734.0
Iteration:  183 Predict:  985 Ground Tru

Iteration:  326 Predict:  64 Ground Truth:  42.0
Iteration:  327 Predict:  397 Ground Truth:  397.0
Iteration:  328 Predict:  384 Ground Truth:  383.0
Iteration:  329 Predict:  720 Ground Truth:  720.0
Iteration:  330 Predict:  753 Ground Truth:  668.0
Iteration:  331 Predict:  738 Ground Truth:  738.0
Iteration:  332 Predict:  143 Ground Truth:  143.0
Iteration:  333 Predict:  994 Ground Truth:  923.0
Iteration:  334 Predict:  843 Ground Truth:  843.0
Iteration:  335 Predict:  820 Ground Truth:  820.0
Iteration:  336 Predict:  487 Ground Truth:  485.0
Iteration:  337 Predict:  790 Ground Truth:  790.0
Iteration:  338 Predict:  914 Ground Truth:  529.0
Iteration:  339 Predict:  37 Ground Truth:  37.0
Iteration:  340 Predict:  848 Ground Truth:  848.0
Iteration:  341 Predict:  626 Ground Truth:  626.0
Iteration:  342 Predict:  186 Ground Truth:  186.0
Iteration:  343 Predict:  761 Ground Truth:  761.0
Iteration:  344 Predict:  544 Ground Truth:  593.0
Iteration:  345 Predict:  302 Groun

Iteration:  488 Predict:  789 Ground Truth:  789.0
Iteration:  489 Predict:  714 Ground Truth:  714.0
Iteration:  490 Predict:  830 Ground Truth:  830.0
Iteration:  491 Predict:  52 Ground Truth:  441.0
Iteration:  492 Predict:  966 Ground Truth:  966.0
Iteration:  493 Predict:  767 Ground Truth:  767.0
Iteration:  494 Predict:  100 Ground Truth:  100.0
Iteration:  495 Predict:  6 Ground Truth:  6.0
Iteration:  496 Predict:  502 Ground Truth:  502.0
Iteration:  497 Predict:  495 Ground Truth:  495.0
Iteration:  498 Predict:  547 Ground Truth:  547.0
Iteration:  499 Predict:  31 Ground Truth:  31.0
Iteration:  500 Predict:  102 Ground Truth:  102.0
Iteration:  501 Predict:  53 Ground Truth:  53.0
Iteration:  502 Predict:  675 Ground Truth:  315.0
Iteration:  503 Predict:  834 Ground Truth:  834.0
Iteration:  504 Predict:  592 Ground Truth:  592.0
Iteration:  505 Predict:  301 Ground Truth:  301.0
Iteration:  506 Predict:  141 Ground Truth:  141.0
Iteration:  507 Predict:  507 Ground Tru

Iteration:  650 Predict:  386 Ground Truth:  386.0
Iteration:  651 Predict:  695 Ground Truth:  596.0
Iteration:  652 Predict:  970 Ground Truth:  970.0
Iteration:  653 Predict:  788 Ground Truth:  777.0
Iteration:  654 Predict:  216 Ground Truth:  216.0
Iteration:  655 Predict:  783 Ground Truth:  783.0
Iteration:  656 Predict:  169 Ground Truth:  169.0
Iteration:  657 Predict:  148 Ground Truth:  148.0
Iteration:  658 Predict:  699 Ground Truth:  269.0
Iteration:  659 Predict:  313 Ground Truth:  228.0
Iteration:  660 Predict:  131 Ground Truth:  147.0
Iteration:  661 Predict:  227 Ground Truth:  227.0
Iteration:  662 Predict:  252 Ground Truth:  252.0
Iteration:  663 Predict:  564 Ground Truth:  244.0
Iteration:  664 Predict:  5 Ground Truth:  5.0
Iteration:  665 Predict:  709 Ground Truth:  544.0
Iteration:  666 Predict:  376 Ground Truth:  219.0
Iteration:  667 Predict:  139 Ground Truth:  139.0
Iteration:  668 Predict:  628 Ground Truth:  612.0
Iteration:  669 Predict:  686 Groun

...

Iteration:  49319 Predict:  108 Ground Truth:  108.0
Iteration:  49320 Predict:  376 Ground Truth:  376.0
Iteration:  49321 Predict:  592 Ground Truth:  592.0
Iteration:  49322 Predict:  104 Ground Truth:  104.0
Iteration:  49323 Predict:  189 Ground Truth:  189.0
Iteration:  49324 Predict:  822 Ground Truth:  844.0
Iteration:  49325 Predict:  191 Ground Truth:  191.0
Iteration:  49326 Predict:  60 Ground Truth:  60.0
Iteration:  49327 Predict:  711 Ground Truth:  232.0
Iteration:  49328 Predict:  723 Ground Truth:  723.0
Iteration:  49329 Predict:  550 Ground Truth:  511.0
Iteration:  49330 Predict:  216 Ground Truth:  216.0
Iteration:  49331 Predict:  81 Ground Truth:  81.0
Iteration:  49332 Predict:  476 Ground Truth:  476.0
Iteration:  49333 Predict:  84 Ground Truth:  84.0
Iteration:  49334 Predict:  572 Ground Truth:  572.0
Iteration:  49335 Predict:  766 Ground Truth:  766.0
Iteration:  49336 Predict:  899 Ground Truth:  899.0
Iteration:  49337 Predict:  427 Ground Truth:  429.0

Iteration:  49475 Predict:  921 Ground Truth:  921.0
Iteration:  49476 Predict:  190 Ground Truth:  190.0
Iteration:  49477 Predict:  604 Ground Truth:  606.0
Iteration:  49478 Predict:  508 Ground Truth:  508.0
Iteration:  49479 Predict:  429 Ground Truth:  432.0
Iteration:  49480 Predict:  997 Ground Truth:  997.0
Iteration:  49481 Predict:  708 Ground Truth:  708.0
Iteration:  49482 Predict:  201 Ground Truth:  201.0
Iteration:  49483 Predict:  133 Ground Truth:  133.0
Iteration:  49484 Predict:  45 Ground Truth:  45.0
Iteration:  49485 Predict:  747 Ground Truth:  302.0
Iteration:  49486 Predict:  685 Ground Truth:  308.0
Iteration:  49487 Predict:  427 Ground Truth:  427.0
Iteration:  49488 Predict:  991 Ground Truth:  991.0
Iteration:  49489 Predict:  319 Ground Truth:  319.0
Iteration:  49490 Predict:  676 Ground Truth:  375.0
Iteration:  49491 Predict:  691 Ground Truth:  897.0
Iteration:  49492 Predict:  342 Ground Truth:  344.0
Iteration:  49493 Predict:  563 Ground Truth:  5

Iteration:  49631 Predict:  317 Ground Truth:  317.0
Iteration:  49632 Predict:  708 Ground Truth:  708.0
Iteration:  49633 Predict:  277 Ground Truth:  277.0
Iteration:  49634 Predict:  469 Ground Truth:  469.0
Iteration:  49635 Predict:  182 Ground Truth:  48.0
Iteration:  49636 Predict:  499 Ground Truth:  499.0
Iteration:  49637 Predict:  631 Ground Truth:  632.0
Iteration:  49638 Predict:  400 Ground Truth:  400.0
Iteration:  49639 Predict:  207 Ground Truth:  207.0
Iteration:  49640 Predict:  705 Ground Truth:  705.0
Iteration:  49641 Predict:  19 Ground Truth:  19.0
Iteration:  49642 Predict:  58 Ground Truth:  58.0
Iteration:  49643 Predict:  746 Ground Truth:  893.0
Iteration:  49644 Predict:  276 Ground Truth:  565.0
Iteration:  49645 Predict:  460 Ground Truth:  460.0
Iteration:  49646 Predict:  729 Ground Truth:  729.0
Iteration:  49647 Predict:  728 Ground Truth:  728.0
Iteration:  49648 Predict:  805 Ground Truth:  805.0
Iteration:  49649 Predict:  70 Ground Truth:  70.0


Iteration:  49787 Predict:  61 Ground Truth:  61.0
Iteration:  49788 Predict:  282 Ground Truth:  281.0
Iteration:  49789 Predict:  572 Ground Truth:  572.0
Iteration:  49790 Predict:  702 Ground Truth:  702.0
Iteration:  49791 Predict:  196 Ground Truth:  196.0
Iteration:  49792 Predict:  955 Ground Truth:  955.0
Iteration:  49793 Predict:  702 Ground Truth:  990.0
Iteration:  49794 Predict:  755 Ground Truth:  755.0
Iteration:  49795 Predict:  768 Ground Truth:  768.0
Iteration:  49796 Predict:  569 Ground Truth:  569.0
Iteration:  49797 Predict:  835 Ground Truth:  747.0
Iteration:  49798 Predict:  581 Ground Truth:  338.0
Iteration:  49799 Predict:  69 Ground Truth:  69.0
Iteration:  49800 Predict:  22 Ground Truth:  22.0
Iteration:  49801 Predict:  607 Ground Truth:  607.0
Iteration:  49802 Predict:  392 Ground Truth:  392.0
Iteration:  49803 Predict:  950 Ground Truth:  950.0
Iteration:  49804 Predict:  94 Ground Truth:  94.0
Iteration:  49805 Predict:  260 Ground Truth:  769.0
I

Iteration:  49943 Predict:  334 Ground Truth:  334.0
Iteration:  49944 Predict:  817 Ground Truth:  854.0
Iteration:  49945 Predict:  818 Ground Truth:  530.0
Iteration:  49946 Predict:  337 Ground Truth:  337.0
Iteration:  49947 Predict:  188 Ground Truth:  129.0
Iteration:  49948 Predict:  924 Ground Truth:  924.0
Iteration:  49949 Predict:  769 Ground Truth:  769.0
Iteration:  49950 Predict:  983 Ground Truth:  819.0
Iteration:  49951 Predict:  702 Ground Truth:  220.0
Iteration:  49952 Predict:  756 Ground Truth:  756.0
Iteration:  49953 Predict:  476 Ground Truth:  475.0
Iteration:  49954 Predict:  530 Ground Truth:  676.0
Iteration:  49955 Predict:  86 Ground Truth:  86.0
Iteration:  49956 Predict:  558 Ground Truth:  558.0
Iteration:  49957 Predict:  165 Ground Truth:  165.0
Iteration:  49958 Predict:  176 Ground Truth:  176.0
Iteration:  49959 Predict:  61 Ground Truth:  61.0
Iteration:  49960 Predict:  639 Ground Truth:  640.0
Iteration:  49961 Predict:  408 Ground Truth:  408

In [14]:
# Convert predict_prob, predict_label to numpy arrays
predict_prob = np.array(predict_prob)
predict_label = np.array(predict_label)

# 0 for correct prediction and 1 for wrong prediction
residuals = (predict_label!=y)

In [15]:
# Check the accuracy
Accuracy = ((50000 - sum(residuals))/50000)*100

print("Top-1 Accuracy is: ", Accuracy)

Top-1 Accuracy is:  70.86
